In [ ]:
!pip install datasets

INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 kB 20.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 14.7 MB/s eta 0:00:00


In [ ]:
import gdown

# Google Drive file ID
file_id = "1WwmqaSfBrsBaW8L7ASRe1ew-gTW0hjGS"
# https://drive.google.com/file/d/1WwmqaSfBrsBaW8L7ASRe1ew-gTW0hjGS/view?usp=drive_link
# Construct the download URL
download_url = f"https://drive.google.com/uc?id={file_id}&export=download"

# Output path where the file will be saved
output = "dataset.json"  # Change the name and extension if needed

# Download the file
gdown.download(download_url, output, quiet=False)

print("Download complete!")


Downloading...
From (original): https://drive.google.com/uc?id=1WwmqaSfBrsBaW8L7ASRe1ew-gTW0hjGS&export=download
From (redirected): https://drive.google.com/uc?id=1WwmqaSfBrsBaW8L7ASRe1ew-gTW0hjGS&export=download&confirm=t&uuid=2a6c2c3f-48e3-41ea-8b04-ae8d9cfd69d2
To: /content/dataset.json
100%|██████████| 3.88G/3.88G [01:01<00:00, 62.6MB/s]

Download complete!


In [ ]:
from datasets import load_dataset
dataset = load_dataset("json", data_files="/content/dataset.json")

Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
print(dataset)

DatasetDict({
    train: Dataset({
        features: ['input_ids', 'labels', 'speaker_embeddings'],
        num_rows: 7956
    })
})


In [ ]:
from transformers import SpeechT5Processor, SpeechT5ForTextToSpeech

processor = SpeechT5Processor.from_pretrained("microsoft/speecht5_tts")
model = SpeechT5ForTextToSpeech.from_pretrained("microsoft/speecht5_tts")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


preprocessor_config.json:   0%|          | 0.00/433 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/232 [00:00<?, ?B/s]

spm_char.model:   0%|          | 0.00/238k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/40.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/234 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


config.json:   0%|          | 0.00/2.06k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/585M [00:00<?, ?B/s]

In [ ]:
from dataclasses import dataclass
from typing import Any, Dict, List, Union
import torch

@dataclass
class TTSDataCollatorWithPadding:
    processor: Any

    def __call__(
        self, features: List[Dict[str, Union[List[int], torch.Tensor]]]
    ) -> Dict[str, torch.Tensor]:
        input_ids = [{"input_ids": feature["input_ids"]} for feature in features]
        label_features = [{"input_values": feature["labels"]} for feature in features]
        speaker_features = [feature["speaker_embeddings"] for feature in features]
        # print(input_ids)/ures)
        # for feature in features:
        #   print(feature)
          # print("Raw Input IDs Shape:", feature["input_ids"].shape)
          # print("Raw Labels Shape:", feature["labels"].shape)

        # collate the inputs and targets into a batch
        batch = processor.pad(
            input_ids=input_ids, labels=label_features, return_tensors="pt"
        )

        # replace padding with -100 to ignore loss correctly
        batch["labels"] = batch["labels"].masked_fill(
            batch.decoder_attention_mask.unsqueeze(-1).ne(1), -100
        )

        # not used during fine-tuning
        del batch["decoder_attention_mask"]

        # round down target lengths to multiple of reduction factor
        if model.config.reduction_factor > 1:
            target_lengths = torch.tensor(
                [len(feature["input_values"]) for feature in label_features]
            )
            target_lengths = target_lengths.new(
                [
                    length - length % model.config.reduction_factor
                    for length in target_lengths
                ]
            )
            max_length = max(target_lengths)
            batch["labels"] = batch["labels"][:, :max_length]

        # also add in the speaker embeddings
        batch["speaker_embeddings"] = torch.tensor(speaker_features)

        return batch

In [ ]:
# from transformers import SpeechT5ForTextToSpeech

# model = SpeechT5ForTextToSpeech.from_pretrained(checkpoint)

In [ ]:
data_collator = TTSDataCollatorWithPadding(processor=processor)

In [ ]:
features = [
    dataset["train"][0],
    dataset["train"][1],
    dataset["train"][20],
]

batch = data_collator(features)

{'input_ids': [4, 25, 16, 11, 7, 13, 10, 4, 21, 8, 4, 25, 13, 7, 9, 17, 11, 4, 15, 8, 9, 14, 8, 9, 4, 9, 5, 37, 6, 4, 20, 5, 5, 28, 4, 25, 5, 19, 8, 13, 5, 4, 11, 10, 18, 4, 17, 8, 18, 4, 25, 7, 17, 28, 4, 14, 10, 19, 19, 5, 13, 5, 9, 6, 4, 6, 22, 24, 5, 12, 4, 8, 19, 4, 7, 15, 17, 8, 11, 8, 15, 4, 21, 8, 4, 7, 19, 19, 5, 17, 6, 2], 'labels': [[-3.0890221596, -3.0977807045, -2.9755175114, -2.9620761871, -2.8892481327, -3.2008857727, -2.8452796936, -3.1479005814, -2.597782135, -2.3779006004, -2.6780164242, -2.381772995, -2.5191822052, -2.6377174854, -2.6177659035, -3.0032000542, -3.8633322716, -3.7534477711, -3.2982439995, -2.9025335312, -2.8296108246, -2.8092360497, -2.7823753357, -2.994124651, -3.3047301769, -3.2956187725, -3.0905146599, -3.2029197216, -3.2632451057, -3.2479376793, -3.5034041405, -4.0386171341, -3.8182041645, -3.9559936523, -3.8604383469, -3.4203336239, -3.0469748974, -3.0995600224, -3.4325118065, -3.3192949295, -3.1054189205, -3.2775807381, -3.0063796043, -2.79495906

In [ ]:
{k:v.shape for k,v in batch.items()}

{'input_ids': torch.Size([3, 98]),
 'attention_mask': torch.Size([3, 98]),
 'labels': torch.Size([3, 384, 80]),
 'speaker_embeddings': torch.Size([3, 512])}

In [ ]:
dataset = dataset["train"].train_test_split(test_size=0.1)
print(dataset)

DatasetDict({
    train: Dataset({
        features: ['input_ids', 'labels', 'speaker_embeddings'],
        num_rows: 7160
    })
    test: Dataset({
        features: ['input_ids', 'labels', 'speaker_embeddings'],
        num_rows: 796
    })
})


In [ ]:
def is_not_too_long(input_ids):
    input_length = len(input_ids)
    return input_length < 200

dataset = dataset.filter(is_not_too_long, input_columns=["input_ids"])

Filter:   0%|          | 0/7160 [00:00<?, ? examples/s]

Filter:   0%|          | 0/796 [00:00<?, ? examples/s]

In [ ]:
from functools import partial

# disable cache during training since it's incompatible with gradient checkpointing
model.config.use_cache = False

# set language and task for generation and re-enable cache
model.generate = partial(model.generate, use_cache=True)

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="/content/drive/MyDrive",  # This will create a new repo on the Hub
    per_device_train_batch_size=4,
    gradient_accumulation_steps=8,
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=4000,
    gradient_checkpointing=True,
    fp16=True,
    evaluation_strategy="steps",
    per_device_eval_batch_size=2,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    greater_is_better=False,
    label_names=["labels"],
    push_to_hub=True,  # Push checkpoints to the Hugging Face Hub
    # hub_model_id="solvebyte/solvebyte-pidginTTS",  # Your repo name on HF Hub
    hub_strategy="every_save",  # Push to hub after every save
)


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    data_collator=data_collator,
    tokenizer=processor.tokenizer,
)

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)
max_steps is given, it will override any value given in num_train_epochs


In [ ]:
trainer.train()

/usr/local/lib/python3.10/dist-packages/torch/_dynamo/eval_frame.py:600: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  return fn(*args, **kwargs)
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:295: FutureWarning: `torch.cpu.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cpu', args...)` instead.
  with torch.enable_grad(), device_autocast_ctx, torch.cpu.amp.autocast(**ctx.cpu_autocast_kwargs):  # type: ignore[attr-defined]


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 1876}
Your generation config was originally created from the model config, but the model config has changed since then. Unless you pass the `generation_config` argument to this model's `generate` calls, they will revert to the legacy behavior where the base `generate` parameterization is loaded from the model config instead. To avoid this behavior and this warning, we recommend you to overwrite the generation config model attribute before calling the model's `save_pretrained`, preferably also removing any generation kwargs from the model config. This warning will be raised to an exception in v4.41.
/usr/local/lib/python3.10/dist-packages/torch/_dynamo/e

In [ ]:
|